<h1>A new restaurant in Palma </h1>
<p>Created by: Carlos Reche </p>

In [2]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Solving environment: done

## Package Plan ##

  environment location: /opt/conda/envs/Python36

  added / updated specs: 
    - geopy


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    ca-certificates-2019.11.28 |       hecc5488_0         145 KB  conda-forge
    geopy-1.21.0               |             py_0          58 KB  conda-forge
    openssl-1.1.1d             |       h516909a_0         2.1 MB  conda-forge
    certifi-2019.11.28         |           py36_0         149 KB  conda-forge
    geographiclib-1.50         |             py_0          34 KB  conda-forge
    ------------------------------------------------------------
                                           Total:         2.5 MB

The following NEW packages will be INSTALLED:

    geographiclib:   1.50-py_0         conda-forge
    geopy:           1.21.0-py_0       conda-forge

The following packages will be UPDATED:

    ca-

<h1> 1. Import information of the neighborhoods</h1>

It is used a table uploaded to an IBM Cloud account. So first we get that table to get the different neighbourhoods and ther latitude and longitude

In [3]:
!pip install --user ipython-sql
!pip install --user ibm_db
!pip install --user ibm_db_sa

%load_ext sql
%sql ibm_db_sa://jwk01675:j%2Bgrwkx0lpz8kz9v@dashdb-txn-sbox-yp-lon02-02.services.eu-gb.bluemix.net:50000/BLUDB
            

     |████████████████████████████████| 40kB 5.2MB/s eta 0:00:01
  Stored in directory: /home/dsxuser/.cache/pip/wheels/80/34/1c/3967380d9676d162cb59513bd9dc862d0584e045a162095606
Successfully built prettytable
  Consider adding this directory to PATH or, if you prefer to suppress this warning, use --no-warn-script-location.


'Connected: jwk01675@BLUDB'

In [4]:
sql=%sql SELECT * FROM palma_coord 

 * ibm_db_sa://jwk01675:***@dashdb-txn-sbox-yp-lon02-02.services.eu-gb.bluemix.net:50000/BLUDB
Done.


In [5]:
nh=pd.DataFrame(sql)
nh.columns=["Neighborhood","Latitude","Longitude"]
nh.head(5)

Neighborhood   Latitude Longitude
0  Sa Calatrava  39.566042  2.653460
1          Cort  39.569745  2.650053
2     Jaime III  39.572926  2.642615
3          Cort  39.569745  2.650053
4      La Missi  39.573472  2.651218

In [6]:
nh = nh.convert_objects(convert_numeric=True)
nh.dtypes

/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:1: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.
  if __name__ == '__main__':


Neighborhood     object
Latitude        float64
Longitude       float64
dtype: object

In [7]:
address = 'Palma de Mallorca '
geolocator = Nominatim(user_agent="palma")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude


In [136]:
map_palma = folium.Map(location=[latitude, longitude], zoom_start=15)
for n in range (1,len(nh)):
    lat=nh.iat[n-1,1]
    lng=nh.iat[n-1,2]
    label = folium.Popup(nh.iat[n-1,0], parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_palma)  
    
    
map_palma

To get only the centre of the city we will delete the neighborhoods outside Via Cintura (red line)

In [8]:
nh=nh[nh["Longitude"] <= 2.675]
nh=nh[nh["Latitude"] <= 39.596405]
nh=nh[nh["Longitude"] >= 2.624151]


In [9]:
map_palma = folium.Map(location=[latitude, longitude], zoom_start=15)
for n in range (1,len(nh)):
    lat=nh.iat[n-1,1]
    lng=nh.iat[n-1,2]
    label = folium.Popup(nh.iat[n-1,0], parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_palma)  
    
    
map_palma

<h1>2. Get info about venues </h1>

Foursquare will be used to get the places of each of the neighbours of our list.

In [10]:
CLIENT_ID = 'LBMHKN303KP00R04KUD2KVTOOJ0JLBX50HWGEJCW2213TA1E' # your Foursquare ID
CLIENT_SECRET = 'PZRCB3TRSUNKTYUFOBPARHVOP55RDKNCVSF2T4V1MTI12FXW' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: LBMHKN303KP00R04KUD2KVTOOJ0JLBX50HWGEJCW2213TA1E
CLIENT_SECRET:PZRCB3TRSUNKTYUFOBPARHVOP55RDKNCVSF2T4V1MTI12FXW


In [11]:
def getNearbyVenues(names, latitudes, longitudes, radius=500,LIMIT=1000):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [12]:
palma_venues = getNearbyVenues(names=nh['Neighborhood'],
                                   latitudes=nh['Latitude'],
                                   longitudes=nh['Longitude']
                                  )


Sa Calatrava
Cort
Jaime III
Cort
La Missi
Monti-sion
Pla�a dels Patins
Puig de Sant Pere
Sant Jaume
Sant Nicolau
La Seu
Sindicat
Can Capes
Estadio Balear
Foners
Els Hostalets
Marqu�s de la Fontsanta
Pedro Garau
Pol�gono de Levante
Rafal Vell
La Soledad
Son Canals
Son Fortesa Norte
Son Fortesa Sur
Son Gotleu
El Vivero
Amanecer
Arxiduc
Bons Aires
Camp Red
Cas Capiscol
L'Oliverar
Plaza de Toros
Son Oliva y Son Sardina
Can Pere Antoni
Camp d'en Serralta
El Fort
El Jonquet
Santa Catalina
Son Armadams
Son Cotoner
Son Dameto
Son Dureta
Son Espanyolet
Son Flor


In [13]:
print(palma_venues.shape)
palma_venues.head()

(1983, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  Sa Calatrava              39.566042                 2.65346   
1  Sa Calatrava              39.566042                 2.65346   
2  Sa Calatrava              39.566042                 2.65346   
3  Sa Calatrava              39.566042                 2.65346   
4  Sa Calatrava              39.566042                 2.65346   

                         Venue  Venue Latitude  Venue Longitude  \
0                Temple Natura       39.567718         2.654483   
1  AMADIP ESMENT (cafè botiga)       39.568100         2.654424   
2             Hotel Es Princep       39.565613         2.655407   
3       Plaça de Sant Francesc       39.568749         2.651912   
4          Hotel Sant Francesc       39.569029         2.652439   

                  Venue Category  
0  Vegetarian / Vegan Restaurant  
1                           Café  
2                          Hotel  
3                          Plaza  
4                          Hotel

In [14]:
palma_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  Venue  \
Neighborhood                                                                    
Amanecer                                    10                      10     10   
Arxiduc                                      7                       7      7   
Bons Aires                                  64                      64     64   
Camp Red                                    34                      34     34   
Camp d'en Serralta                          32                      32     32   
Can Capes                                   11                      11     11   
Can Pere Antoni                             20                      20     20   
Cas Capiscol                                22                      22     22   
Cort                                       200                     200    200   
El Fort                                     68                      68     68   
El Jonquet                                 100                     100    100   
El Vivero                                    8                       8      8   
Els Hostalets                               16                      16     16   
Estadio Balear                             100                     100    100   
Foners                                      43                      43     43   
Jaime III                                  100                     100    100   
L'Oliverar                                  13                      13     13   
La Missi                                   100                     100    100   
La Seu                                     100                     100    100   
La Soledad                                   4                       4      4   
Marqu�s de la Fontsanta                     53                      53     53   
Monti-sion                                  74                      74     74   
Pedro Garau                                 18                      18     18   
Plaza de Toros                              23                      23     23   
Pla�a dels Patins                           51                      51     51   
Pol�gono de Levante                          3                       3      3   
Puig de Sant Pere                          100                     100    100   
Rafal Vell                                  13                      13     13   
Sa Calatrava                                46                      46     46   
Sant Jaume                                 100                     100    100   
Sant Nicolau                               100                     100    100   
Santa Catalina                             100                     100    100   
Sindicat                                    59                      59     59   
Son Armadams                                68                      68     68   
Son Canals                                  11                      11     11   
Son Cotoner                                 18                      18     18   
Son Dameto                                  22                      22     22   
Son Dureta                                   7                       7      7   
Son Espanyolet                               4                       4      4   
Son Flor                                    16                      16     16   
Son Fortesa Norte                           19                      19     19   
Son Fortesa Sur                             12                      12     12   
Son Gotleu                                   7                       7      7   
Son Oliva y Son Sardina                      7                       7      7   

                         Venue Latitude  Venue Longitude  Venue Category  
Neighborhood                                                              
Amanecer                             10               10              10  
Arxiduc                               7                7               7 

We can see the results of Foursquare in a map

In [15]:
map_palma = folium.Map(location=[39.5695818, 2.6500745], zoom_start=15)

# add markers to map
for lat, lng, label in zip(palma_venues['Venue Latitude'], palma_venues['Venue Longitude'], palma_venues['Venue']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_palma)  
    
map_palma

<h1>4. Treat the info </h1>

With all these info we can cluster each of the neighborhoods depending on the results of Foursquare. First we are going to treat the data to been able to see something more before making the process of clustering.

In [16]:
# one hot encoding
palma_onehot = pd.get_dummies(palma_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
palma_onehot['Neighborhood'] = palma_venues['Neighborhood'] 

# move neighborhood column to the first column

#fixed_columns = [palma_onehot.columns[-1]] + list(palma_onehot.columns[:-1])
#palma_onehot = palma_onehot[fixed_columns]
#palma_onehot.head()

In [17]:
palma_grouped = palma_onehot.groupby('Neighborhood').mean().reset_index()


In [18]:
palma_grouped.head()

Neighborhood  American Restaurant  Argentinian Restaurant  \
0            Amanecer             0.000000                0.000000   
1             Arxiduc             0.000000                0.000000   
2          Bons Aires             0.015625                0.015625   
3            Camp Red             0.029412                0.000000   
4  Camp d'en Serralta             0.000000                0.000000   

   Art Gallery  Art Museum  Asian Restaurant  BBQ Joint  Bagel Shop    Bakery  \
0          0.0         0.0               0.0        0.0         0.0  0.000000   
1          0.0         0.0               0.0        0.0         0.0  0.000000   
2          0.0         0.0               0.0        0.0         0.0  0.046875   
3          0.0         0.0               0.0        0.0         0.0  0.000000   
4          0.0         0.0               0.0        0.0         0.0  0.000000   

        Bar  Basketball Court  Beach  Beach Bar  Bed & Breakfast  Beer Bar  \
0  0.000000               0.0    0.0        0.0              0.0       0.0   
1  0.000000               0.0    0.0        0.0              0.0       0.0   
2  0.031250               0.0    0.0        0.0              0.0       0.0   
3  0.058824               0.0    0.0        0.0              0.0       0.0   
4  0.031250               0.0    0.0        0.0              0.0       0.0   

   Beer Garden  Bistro  Bookstore  Boutique  Brazilian Restaurant  \
0          0.0     0.0        0.0       0.0                   0.0   
1          0.0     0.0        0.0       0.0                   0.0   
2          0.0     0.0        0.0       0.0                   0.0   
3          0.0     0.0        0.0       0.0                   0.0   
4          0.0     0.0        0.0       0.0                   0.0   

   Breakfast Spot   Brewery  Burger Joint  Burrito Place      Café  \
0             0.0  0.000000      0.000000            0.0  0.100000   
1             0.0  0.142857      0.000000            0.0  0.142857   
2             0.0  0.000000      0.000000            0.0  0.125000   
3             0.0  0.000000      0.029412            0.0  0.147059   
4             0.0  0.000000      0.062500            0.0  0.031250   

   Cajun / Creole Restaurant  Candy Store  Casino  Chinese Restaurant  \
0                        0.0          0.0     0.0             0.00000   
1                        0.0          0.0     0.0             0.00000   
2                        0.0          0.0     0.0             0.00000   
3                        0.0          0.0     0.0             0.00000   
4                        0.0          0.0     0.0             0.03125   

   Clothing Store  Cocktail Bar  Coffee Shop  Convenience Store  \
0             0.1      0.000000     0.000000                0.0   
1             0.0      0.000000     0.000000                0.0   
2             0.0      0.015625     0.015625                0.0   
3             0.0      0.000000     0.029412                0.0   
4             0.0      0.062500     0.000000                0.0   

   Cosmetics Shop  Creperie  Deli / Bodega  Department Store    Diner  \
0             0.0   0.00000            0.0               0.0  0.10000   
1             0.0   0.00000            0.0               0.0  0.00000   
2             0.0   0.00000            0.0               0.0  0.00000   
3             0.0   0.00000            0.0               0.0  0.00000   
4             0.0   0.03125            0.0               0.0  0.03125   

   Dive Bar  Electronics Store  Event Space  Falafel Restaurant  \
0       0.0                0.0          0.0            0.000000   
1       0.0                0.0          0.0            0.000000   
2       0.0                0.0          0.0            0.000000   
3       0.0                0.0          0.0            0.029412   
4       0.0                0.0          0.0            0.000000   

   Farmers Market  Fast Food Restaurant  Flower Shop  Food & Drink Shop  \
0        0.000000                   0

In [19]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [20]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = palma_grouped['Neighborhood']

for ind in np.arange(palma_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(palma_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue     2nd Most Common Venue  \
0            Amanecer            Restaurant               Supermarket   
1             Arxiduc                  Pool  Mediterranean Restaurant   
2          Bons Aires                  Café                Restaurant   
3            Camp Red                  Café               Pizza Place   
4  Camp d'en Serralta            Restaurant        Italian Restaurant   

  3rd Most Common Venue     4th Most Common Venue 5th Most Common Venue  \
0      Tapas Restaurant  Mediterranean Restaurant                 Diner   
1                  Park                      Café               Brewery   
2                 Plaza          Tapas Restaurant                Bakery   
3                 Plaza          Sushi Restaurant                   Bar   
4          Cocktail Bar          Tapas Restaurant          Burger Joint   

      6th Most Common Venue     7th Most Common Venue 8th Most Common Venue  \
0                      Pool            Clothing Store                  Café   
1              Gourmet Shop               Gas Station        Hardware Store   
2               Pizza Place  Mediterranean Restaurant      Sushi Restaurant   
3       American Restaurant              Burger Joint        Farmers Market   
4  Mediterranean Restaurant          Sushi Restaurant    Spanish Restaurant   

  9th Most Common Venue 10th Most Common Venue  
0     Food & Drink Shop            Flower Shop  
1       Harbor / Marina                  Diner  
2           Snack Place      Indian Restaurant  
3         Shopping Mall             Food Court  
4                Resort                   Café

<h1>5.Cluster</h1>

With the info seen, we are going to cluster the neighboors

In [21]:
# set number of clusters
kclusters = 8

palma_grouped_clustering = palma_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(palma_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([7, 3, 3, 3, 7, 3, 7, 1, 7, 7], dtype=int32)

In [22]:
# add clustering labels

neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

palma_merged = nh

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
palma_merged = palma_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

palma_merged.head() # check the last columns!

Neighborhood   Latitude  Longitude  Cluster Labels 1st Most Common Venue  \
0  Sa Calatrava  39.566042   2.653460               0                 Hotel   
1          Cort  39.569745   2.650053               7      Tapas Restaurant   
2     Jaime III  39.572926   2.642615               7    Spanish Restaurant   
3          Cort  39.569745   2.650053               7      Tapas Restaurant   
4      La Missi  39.573472   2.651218               7      Tapas Restaurant   

  2nd Most Common Venue     3rd Most Common Venue 4th Most Common Venue  \
0                  Café          Tapas Restaurant                 Plaza   
1                 Plaza                      Café                 Hotel   
2      Tapas Restaurant  Mediterranean Restaurant                 Hotel   
3                 Plaza                      Café                 Hotel   
4                  Café                     Hotel                 Plaza   

  5th Most Common Venue     6th Most Common Venue 7th Most Common Venue  \
0           Coffee Shop                      Park    Spanish Restaurant   
1    Spanish Restaurant                Restaurant                   Bar   
2            Restaurant              Cocktail Bar                   Bar   
3    Spanish Restaurant                Restaurant                   Bar   
4            Restaurant  Mediterranean Restaurant    Spanish Restaurant   

  8th Most Common Venue     9th Most Common Venue    10th Most Common Venue  
0             Gift Shop  Mediterranean Restaurant                  Beer Bar  
1           Coffee Shop            Ice Cream Shop  Mediterranean Restaurant  
2    Italian Restaurant          Sushi Restaurant                      Café  
3           Coffee Shop            Ice Cream Shop  Mediterranean Restaurant  
4           Coffee Shop                       Bar             Deli / Bodega

In [23]:
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=15)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(palma_merged['Latitude'], palma_merged['Longitude'], palma_merged['Neighborhood'], palma_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [25]:
palma_merged.sort_values(by=['Cluster Labels'])

Neighborhood   Latitude  Longitude  Cluster Labels  \
0              Sa Calatrava  39.566042   2.653460               0   
70               Son Dureta  39.571788   2.624151               0   
5                Monti-sion  39.567139   2.652638               0   
34             Cas Capiscol  39.592272   2.645739               1   
29                El Vivero  39.596405   2.643080               1   
21               La Soledad  39.571111   2.673611               1   
42  Son Oliva y Son Sardina  39.586806   2.663722               2   
38               L'Oliverar  39.590278   2.662222               2   
25          Son Fortesa Sur  39.583365   2.667371               2   
20               Rafal Vell  39.590278   2.662222               2   
24        Son Fortesa Norte  39.584174   2.669409               2   
11                 Sindicat  39.572525   2.656396               3   
39           Plaza de Toros  39.583444   2.656667               3   
33                 Camp Red  39.584220   2.650056               3   
32               Bons Aires  39.581361   2.649886               3   
26               Son Gotleu  39.578042   2.673226               3   
22               Son Canals  39.577863   2.665908               3   
31                  Arxiduc  39.588233   2.659021               3   
17  Marqu�s de la Fontsanta  39.578444   2.658841               3   
12                Can Capes  39.580935   2.669432               3   
18              Pedro Garau  39.575046   2.664641               3   
15            Els Hostalets  39.580948   2.663936               3   
14                   Foners  39.568833   2.659779               3   
72                 Son Flor  39.591512   2.626946               4   
69               Son Dameto  39.580256   2.629523               4   
68              Son Cotoner  39.581906   2.633111               4   
19      Pol�gono de Levante  39.567222   2.672500               5   
71           Son Espanyolet  39.575026   2.629206               6   
10                   La Seu  39.567473   2.648168               7   
1                      Cort  39.569745   2.650053               7   
9              Sant Nicolau  39.570780   2.648449               7   
8                Sant Jaume  39.572664   2.647893               7   
67             Son Armadams  39.568906   2.630230               7   
65           Santa Catalina  39.571370   2.637491               7   
62               El Jonquet  39.569855   2.637490               7   
60                  El Fort  39.569656   2.631842               7   
59       Camp d'en Serralta  39.575889   2.639167               7   
51          Can Pere Antoni  39.561670   2.666114               7   
2                 Jaime III  39.572926   2.642615               7   
7         Puig de Sant Pere  39.569444   2.642778               7   
4                  La Missi  39.573472   2.651218               7   
13           Estadio Balear  39.569582   2.650075               7   
6         Pla�a dels Patins  39.575844   2.648979               7   
30                 Amanecer  39.593045   2.656629               7   
3                      Cort  39.569745   2.650053               7   

       1st Most Common Venue          2nd Most Common Venue  \
0                      Hotel                           Café   
70                     Hotel                      BBQ Joint   
5                      Hotel               Tapas Restaurant   
34               Pizza Place              Electronics Store   
29      Fast Food Restaurant                 Breakfast Spot   
21  Mediterranean Restaurant                   Soccer Field   
42               Gas Station                 Ice Cream Shop   
38               Supermarket                 Breakfast Spot   
25               Supermarket                 Ice Cream Shop   
20               Supermarket                 Breakfast Spot   
24               Supermarket                           Park   
11                      Café               Tapas Restaurant   
39       Japanese Res

<h1>6.Restaurants</h1>

Now we are going to make a clustering but only getting information of restaurants

In [27]:
palma_venues['Test_Flag'] = np.where(palma_venues['Venue Category'].str.contains(" Restaurant", case=False, na=False), 'T', '')
palma_venues.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  Sa Calatrava              39.566042                 2.65346   
1  Sa Calatrava              39.566042                 2.65346   
2  Sa Calatrava              39.566042                 2.65346   
3  Sa Calatrava              39.566042                 2.65346   
4  Sa Calatrava              39.566042                 2.65346   

                         Venue  Venue Latitude  Venue Longitude  \
0                Temple Natura       39.567718         2.654483   
1  AMADIP ESMENT (cafè botiga)       39.568100         2.654424   
2             Hotel Es Princep       39.565613         2.655407   
3       Plaça de Sant Francesc       39.568749         2.651912   
4          Hotel Sant Francesc       39.569029         2.652439   

                  Venue Category Test_Flag  
0  Vegetarian / Vegan Restaurant         T  
1                           Café            
2                          Hotel            
3                          Plaza            
4                          Hotel

In [28]:
palma_rest=palma_venues.loc[palma_venues["Test_Flag"]=="T"]

In [29]:
map_palma = folium.Map(location=[39.5695818, 2.6500745], zoom_start=15)

# add markers to map
for lat, lng, label in zip(palma_rest['Venue Latitude'], palma_rest['Venue Longitude'], palma_rest['Venue']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_palma)  
    
map_palma

In [30]:
# one hot encoding
palma_onehot = pd.get_dummies(palma_rest[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
palma_onehot['Neighborhood'] = palma_rest['Neighborhood'] 

# move neighborhood column to the first column

#fixed_columns = [palma_onehot.columns[-1]] + list(palma_onehot.columns[:-1])
#palma_onehot = palma_onehot[fixed_columns]
#palma_onehot.head()

In [31]:
palma_grouped = palma_onehot.groupby('Neighborhood').mean().reset_index()

In [32]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = palma_grouped['Neighborhood']

for ind in np.arange(palma_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(palma_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood     1st Most Common Venue  \
0            Amanecer  Mediterranean Restaurant   
1             Arxiduc  Mediterranean Restaurant   
2          Bons Aires          Tapas Restaurant   
3            Camp Red          Sushi Restaurant   
4  Camp d'en Serralta        Italian Restaurant   

           2nd Most Common Venue          3rd Most Common Venue  \
0               Tapas Restaurant  Vegetarian / Vegan Restaurant   
1  Vegetarian / Vegan Restaurant             Turkish Restaurant   
2               Sushi Restaurant       Mediterranean Restaurant   
3            American Restaurant            Japanese Restaurant   
4               Tapas Restaurant               Sushi Restaurant   

    4th Most Common Venue     5th Most Common Venue  \
0  Argentinian Restaurant          Asian Restaurant   
1  Argentinian Restaurant          Asian Restaurant   
2       Indian Restaurant       Moroccan Restaurant   
3        Tapas Restaurant        Falafel Restaurant   
4      Spanish Restaurant  Mediterranean Restaurant   

           6th Most Common Venue      7th Most Common Venue  \
0           Brazilian Restaurant  Cajun / Creole Restaurant   
1           Brazilian Restaurant  Cajun / Creole Restaurant   
2             Italian Restaurant        Japanese Restaurant   
3      Middle Eastern Restaurant     Argentinian Restaurant   
4  Vegetarian / Vegan Restaurant         Chinese Restaurant   

  8th Most Common Venue      9th Most Common Venue     10th Most Common Venue  
0    Chinese Restaurant         Falafel Restaurant       Fast Food Restaurant  
1    Chinese Restaurant         Falafel Restaurant       Fast Food Restaurant  
2    Turkish Restaurant  Middle Eastern Restaurant        American Restaurant  
3      Asian Restaurant       Brazilian Restaurant  Cajun / Creole Restaurant  
4     French Restaurant          Indian Restaurant        Japanese Restaurant

In [33]:
# set number of clusters
kclusters = 5

palma_grouped_clustering = palma_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(palma_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([2, 4, 0, 0, 0, 0, 0, 2, 0, 0], dtype=int32)

In [34]:
# add clustering labels

neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

palma_merged = nh

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
palma_merged = palma_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

palma_merged # check the last columns!


Neighborhood   Latitude  Longitude  Cluster Labels  \
0              Sa Calatrava  39.566042   2.653460             2.0   
1                      Cort  39.569745   2.650053             2.0   
2                 Jaime III  39.572926   2.642615             0.0   
3                      Cort  39.569745   2.650053             2.0   
4                  La Missi  39.573472   2.651218             2.0   
5                Monti-sion  39.567139   2.652638             2.0   
6         Pla�a dels Patins  39.575844   2.648979             0.0   
7         Puig de Sant Pere  39.569444   2.642778             0.0   
8                Sant Jaume  39.572664   2.647893             2.0   
9              Sant Nicolau  39.570780   2.648449             2.0   
10                   La Seu  39.567473   2.648168             2.0   
11                 Sindicat  39.572525   2.656396             0.0   
12                Can Capes  39.580935   2.669432             NaN   
13           Estadio Balear  39.569582   2.650075             2.0   
14                   Foners  39.568833   2.659779             0.0   
15            Els Hostalets  39.580948   2.663936             0.0   
17  Marqu�s de la Fontsanta  39.578444   2.658841             0.0   
18              Pedro Garau  39.575046   2.664641             0.0   
19      Pol�gono de Levante  39.567222   2.672500             0.0   
20               Rafal Vell  39.590278   2.662222             1.0   
21               La Soledad  39.571111   2.673611             4.0   
22               Son Canals  39.577863   2.665908             0.0   
24        Son Fortesa Norte  39.584174   2.669409             1.0   
25          Son Fortesa Sur  39.583365   2.667371             1.0   
26               Son Gotleu  39.578042   2.673226             NaN   
29                El Vivero  39.596405   2.643080             0.0   
30                 Amanecer  39.593045   2.656629             2.0   
31                  Arxiduc  39.588233   2.659021             4.0   
32               Bons Aires  39.581361   2.649886             0.0   
33                 Camp Red  39.584220   2.650056             0.0   
34             Cas Capiscol  39.592272   2.645739             0.0   
38               L'Oliverar  39.590278   2.662222             1.0   
39           Plaza de Toros  39.583444   2.656667             0.0   
42  Son Oliva y Son Sardina  39.586806   2.663722             1.0   
51          Can Pere Antoni  39.561670   2.666114             0.0   
59       Camp d'en Serralta  39.575889   2.639167             0.0   
60                  El Fort  39.569656   2.631842             0.0   
62               El Jonquet  39.569855   2.637490             0.0   
65           Santa Catalina  39.571370   2.637491             0.0   
67             Son Armadams  39.568906   2.630230             0.0   
68              Son Cotoner  39.581906   2.633111             0.0   
69               Son Dameto  39.580256   2.629523             2.0   
70               Son Dureta  39.571788   2.624151             NaN   
71           Son Espanyolet  39.575026   2.629206             NaN   
72                 Son Flor  39.591512   2.626946             3.0   

       1st Most Common Venue          2nd Most Common Venue  \
0           Tapas Restaurant             Spanish Restaurant   
1           Tapas Restaurant             Spanish Restaurant   
2         Spanish Restaurant               Tapas Restaurant   
3           Tapas Restaurant             Spanish Restaurant   
4           Tapas Restaurant       Mediterranean Restaurant   
5           Tapas Restaurant             Spanish Restaurant   
6   Mediterranean Restaurant               Tapas Restaurant   
7         Spanish Restaurant       Mediterranean Restaurant   
8           Tapas Restaurant             Spanish Restaurant   
9           Tapas Restaurant             Spanish Restaurant   
10        Spanish Restaurant               Tapas Restaurant   
11          Tapas Restaurant            Japanese Restaurant   
12                   

In [35]:
palma_merged=palma_merged.dropna()
palma_merged["Cluster Labels"].astype(int)
palma_merged

Neighborhood   Latitude  Longitude  Cluster Labels  \
0              Sa Calatrava  39.566042   2.653460             2.0   
1                      Cort  39.569745   2.650053             2.0   
2                 Jaime III  39.572926   2.642615             0.0   
3                      Cort  39.569745   2.650053             2.0   
4                  La Missi  39.573472   2.651218             2.0   
5                Monti-sion  39.567139   2.652638             2.0   
6         Pla�a dels Patins  39.575844   2.648979             0.0   
7         Puig de Sant Pere  39.569444   2.642778             0.0   
8                Sant Jaume  39.572664   2.647893             2.0   
9              Sant Nicolau  39.570780   2.648449             2.0   
10                   La Seu  39.567473   2.648168             2.0   
11                 Sindicat  39.572525   2.656396             0.0   
13           Estadio Balear  39.569582   2.650075             2.0   
14                   Foners  39.568833   2.659779             0.0   
15            Els Hostalets  39.580948   2.663936             0.0   
17  Marqu�s de la Fontsanta  39.578444   2.658841             0.0   
18              Pedro Garau  39.575046   2.664641             0.0   
19      Pol�gono de Levante  39.567222   2.672500             0.0   
20               Rafal Vell  39.590278   2.662222             1.0   
21               La Soledad  39.571111   2.673611             4.0   
22               Son Canals  39.577863   2.665908             0.0   
24        Son Fortesa Norte  39.584174   2.669409             1.0   
25          Son Fortesa Sur  39.583365   2.667371             1.0   
29                El Vivero  39.596405   2.643080             0.0   
30                 Amanecer  39.593045   2.656629             2.0   
31                  Arxiduc  39.588233   2.659021             4.0   
32               Bons Aires  39.581361   2.649886             0.0   
33                 Camp Red  39.584220   2.650056             0.0   
34             Cas Capiscol  39.592272   2.645739             0.0   
38               L'Oliverar  39.590278   2.662222             1.0   
39           Plaza de Toros  39.583444   2.656667             0.0   
42  Son Oliva y Son Sardina  39.586806   2.663722             1.0   
51          Can Pere Antoni  39.561670   2.666114             0.0   
59       Camp d'en Serralta  39.575889   2.639167             0.0   
60                  El Fort  39.569656   2.631842             0.0   
62               El Jonquet  39.569855   2.637490             0.0   
65           Santa Catalina  39.571370   2.637491             0.0   
67             Son Armadams  39.568906   2.630230             0.0   
68              Son Cotoner  39.581906   2.633111             0.0   
69               Son Dameto  39.580256   2.629523             2.0   
72                 Son Flor  39.591512   2.626946             3.0   

       1st Most Common Venue          2nd Most Common Venue  \
0           Tapas Restaurant             Spanish Restaurant   
1           Tapas Restaurant             Spanish Restaurant   
2         Spanish Restaurant               Tapas Restaurant   
3           Tapas Restaurant             Spanish Restaurant   
4           Tapas Restaurant       Mediterranean Restaurant   
5           Tapas Restaurant             Spanish Restaurant   
6   Mediterranean Restaurant               Tapas Restaurant   
7         Spanish Restaurant       Mediterranean Restaurant   
8           Tapas Restaurant             Spanish Restaurant   
9           Tapas Restaurant             Spanish Restaurant   
10        Spanish Restaurant               Tapas Restaurant   
11          Tapas Restaurant            Japanese Restaurant   
13          Tapas Restaurant             Spanish Restaurant   
14  Mediterranean Restaurant  Vegetarian / Vegan Restaurant   
15  Mediterranean Restaurant                Thai Restaurant   
17  Mediterranean Restaurant            Japanese Restaurant   
18        Chinese Restaurant            Japan

In [36]:
palma_merged["Cluster Labels"]=palma_merged["Cluster Labels"].astype(int)
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=15)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(palma_merged['Latitude'], palma_merged['Longitude'], palma_merged['Neighborhood'], palma_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters


/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  if __name__ == '__main__':


In [37]:

palma_merged.sort_values(by=['Cluster Labels'])

Neighborhood   Latitude  Longitude  Cluster Labels  \
22               Son Canals  39.577863   2.665908               0   
34             Cas Capiscol  39.592272   2.645739               0   
29                El Vivero  39.596405   2.643080               0   
39           Plaza de Toros  39.583444   2.656667               0   
19      Pol�gono de Levante  39.567222   2.672500               0   
18              Pedro Garau  39.575046   2.664641               0   
17  Marqu�s de la Fontsanta  39.578444   2.658841               0   
15            Els Hostalets  39.580948   2.663936               0   
33                 Camp Red  39.584220   2.650056               0   
11                 Sindicat  39.572525   2.656396               0   
14                   Foners  39.568833   2.659779               0   
59       Camp d'en Serralta  39.575889   2.639167               0   
60                  El Fort  39.569656   2.631842               0   
7         Puig de Sant Pere  39.569444   2.642778               0   
6         Pla�a dels Patins  39.575844   2.648979               0   
62               El Jonquet  39.569855   2.637490               0   
65           Santa Catalina  39.571370   2.637491               0   
67             Son Armadams  39.568906   2.630230               0   
2                 Jaime III  39.572926   2.642615               0   
68              Son Cotoner  39.581906   2.633111               0   
51          Can Pere Antoni  39.561670   2.666114               0   
32               Bons Aires  39.581361   2.649886               0   
42  Son Oliva y Son Sardina  39.586806   2.663722               1   
20               Rafal Vell  39.590278   2.662222               1   
38               L'Oliverar  39.590278   2.662222               1   
24        Son Fortesa Norte  39.584174   2.669409               1   
25          Son Fortesa Sur  39.583365   2.667371               1   
0              Sa Calatrava  39.566042   2.653460               2   
30                 Amanecer  39.593045   2.656629               2   
69               Son Dameto  39.580256   2.629523               2   
13           Estadio Balear  39.569582   2.650075               2   
10                   La Seu  39.567473   2.648168               2   
9              Sant Nicolau  39.570780   2.648449               2   
8                Sant Jaume  39.572664   2.647893               2   
5                Monti-sion  39.567139   2.652638               2   
4                  La Missi  39.573472   2.651218               2   
3                      Cort  39.569745   2.650053               2   
1                      Cort  39.569745   2.650053               2   
72                 Son Flor  39.591512   2.626946               3   
21               La Soledad  39.571111   2.673611               4   
31                  Arxiduc  39.588233   2.659021               4   

       1st Most Common Venue          2nd Most Common Venue  \
22        Mexican Restaurant                Thai Restaurant   
34       American Restaurant               Tapas Restaurant   
29      Fast Food Restaurant             Italian Restaurant   
39       Japanese Restaurant         Argentinian Restaurant   
19        Seafood Restaurant  Vegetarian / Vegan Restaurant   
18        Chinese Restaurant            Japanese Restaurant   
17  Mediterranean Restaurant            Japanese Restaurant   
15  Mediterranean Restaurant                Thai Restaurant   
33          Sushi Restaurant            American Restaurant   
11          Tapas Restaurant            Japanese Restaurant   
14  Mediterranean Restaurant  Vegetarian / Vegan Restaurant   
59        Italian Restaurant               Tapas Restaurant   
60         Indian Restaurant               Tapas Restaurant   
7         Spanish Restaurant       Mediterranean Restaurant   
6   Mediterranean Restaurant               Tapas Restaurant   
62          Tapas Restaurant             Italian Restaurant   
65        Italian Restaurant               Ta

<h1>7. Hotels </h1>

To obtain more info, we can see the distance between the hotels and the restaurants and see if thera are somo close enough to the hotels to see people from the hotels as clients

In [38]:
palma_venues['Test_Flag'] = np.where(palma_venues['Venue Category'].str.contains("Hotel", case=False, na=False), 'T', '')
palma_venues.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  Sa Calatrava              39.566042                 2.65346   
1  Sa Calatrava              39.566042                 2.65346   
2  Sa Calatrava              39.566042                 2.65346   
3  Sa Calatrava              39.566042                 2.65346   
4  Sa Calatrava              39.566042                 2.65346   

                         Venue  Venue Latitude  Venue Longitude  \
0                Temple Natura       39.567718         2.654483   
1  AMADIP ESMENT (cafè botiga)       39.568100         2.654424   
2             Hotel Es Princep       39.565613         2.655407   
3       Plaça de Sant Francesc       39.568749         2.651912   
4          Hotel Sant Francesc       39.569029         2.652439   

                  Venue Category Test_Flag  
0  Vegetarian / Vegan Restaurant            
1                           Café            
2                          Hotel         T  
3                          Plaza            
4                          Hotel         T

In [39]:
palma_rest
palma_hotel=palma_venues[palma_venues["Test_Flag"]=="T"]
palma_hotel.shape

(116, 8)

In [40]:
map_palma = folium.Map(location=[39.5695818, 2.6500745], zoom_start=15)

# add markers to map
for lat, lng, label in zip(palma_hotel['Venue Latitude'], palma_hotel['Venue Longitude'], palma_hotel['Venue']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_palma)  
    
map_palma

In [41]:
palma_hotel2=palma_hotel[["Venue","Venue Latitude","Venue Longitude"]].copy()
palma_hotel2.shape


(116, 3)

In [42]:
palma_rest2=palma_rest[["Venue","Venue Latitude","Venue Longitude", "Test_Flag"]].copy()
palma_rest2.head()

Venue  Venue Latitude  Venue Longitude Test_Flag
0      Temple Natura       39.567718         2.654483         T
11  Ambigú Tapas Bar       39.569912         2.651508         T
21        Quina Creu       39.570360         2.652821         T
22       Molta Barra       39.570208         2.653806         T
26  Se te va la Tapa       39.568943         2.655264         T

In [43]:
fin=pd.DataFrame(columns=["Venue","Hotel","Distance","Latitude","Longitude"])
for i in range(0,len(palma_rest2)):
    min=100000
    hotel="Hola"
    for j in range(1,len(palma_hotel2)):
        palma_rest2.iat[i,3]=((palma_rest2.iat[i,1] - palma_hotel2.iat[j,1])**2 + (palma_rest2.iat[i,2] - palma_hotel2.iat[j,2])**2) 
        if palma_rest2.iat[i,3]<min:
            min=palma_rest2.iat[i,3]
            hotel=palma_hotel2.iat[j,0]
    print(hotel,palma_rest2.iat[i,0])
        #print(palma_rest2.iat[i,0],palma_hotel2.iat[j,0],palma_rest2.iat[i,3])
    fin = fin.append({"Venue": palma_rest2.iat[i,0], "Hotel":hotel,"Distance":min,"Latitude": palma_rest2.iat[i,1], "Longitude": palma_rest2.iat[i,2]}, ignore_index=True)

Hotel Es Princep Temple Natura
Ca'n Cera Ambigú Tapas Bar
Posada Terra Santa Quina Creu
Posada Terra Santa Molta Barra
Posada Terra Santa Se te va la Tapa
Posada Terra Santa La Tortillería
Hotel Mamá Casa Julio
Ca'n Cera Serendipity
Hotel Mamá Restaurant Santa Eulàlia
Hotel Mamá Bar España
Hotel Cort La Rosa
Ca'n Cera Ambigú Tapas Bar
Hotel Born El Camino
Posada Terra Santa Quina Creu
Hotel Born Tast
Hotel Born Bibap
Hotel Mamá Casa Julio
Hotel Born Tast Club
Posada Terra Santa La Tortillería
Posada Terra Santa Plaer Natural
Hotel Born Brondo Architect Restaurant
Posada Terra Santa Molta Barra
Hotel Born Fera
Hotel Born El Pilon
Summum Premium Boutique Hotel Toque de queda
Hotel Born La Quinta Puñeta
Hotel Es Princep Temple Natura
Hotel Born Aromata
Puro Oasis Urbano 13%
Hotel Convent de la Missió Marc Fosh
Puro Oasis Urbano Bruselas
Hotel Born 5 Jotas
Hotel Cort Dehesa Santa Maria
HM Jaime III Made In China
Hotel Hostal Cuba Il Tano
Hotel Hostal Cuba Basmati
Hotel Hostal Cuba Bianco e

Posada Terra Santa Es Baret
Posada Terra Santa Se te va la Tapa
Posada Terra Santa Wok Shack
Posada Terra Santa La Tagliatella
Hotel UR Palacio Avenida He
Hotel UR Palacio Avenida Horapa
Hotel UR Palacio Avenida Hokkaido
Hotel UR Palacio Avenida Kirin
Hotel UR Palacio Avenida Pause
Hotel UR Palacio Avenida Tastau
Hotel UR Palacio Avenida Dehesa Santa Maria
Hotel UR Palacio Avenida Chapultepec
Hotel UR Palacio Avenida Hokkaido
Hotel UR Palacio Avenida Horapa
Hotel UR Palacio Avenida Casa Maruka
Hotel UR Palacio Avenida Daikiya
Hotel UR Palacio Avenida Anatolia
Hotel UR Palacio Avenida El Viejo Vizcacha
Hotel UR Palacio Avenida Bri
Hotel UR Palacio Avenida Palacio
Hotel UR Palacio Avenida Kirin
Hotel UR Palacio Avenida Urbà
Hotel UR Palacio Avenida Bella Istambul
Hotel UR Palacio Avenida Tokio
Hotel UR Palacio Avenida Es Racó de sa Bona Cuina
Hotel UR Palacio Avenida Taj Mahal I
Hotel UR Palacio Avenida Tastau
Hotel UR Palacio Avenida Chapultepec
Hotel UR Palacio Avenida Shi Shan Xuan
Ho

HM Jaime III Coto
Hotel Araxa Restaurante Xin Xin


In [44]:
fin.head()

Venue               Hotel      Distance   Latitude  Longitude
0     Temple Natura    Hotel Es Princep  5.284052e-06  39.567718   2.654483
1  Ambigú Tapas Bar           Ca'n Cera  1.194397e-06  39.569912   2.651508
2        Quina Creu  Posada Terra Santa  4.477991e-07  39.570360   2.652821
3       Molta Barra  Posada Terra Santa  1.639656e-07  39.570208   2.653806
4  Se te va la Tapa  Posada Terra Santa  4.655124e-06  39.568943   2.655264

In [45]:
fin2=fin[fin["Distance"]<0.000001]
fin2

Venue                       Hotel      Distance  \
2                    Quina Creu          Posada Terra Santa  4.477991e-07   
3                   Molta Barra          Posada Terra Santa  1.639656e-07   
5                La Tortillería          Posada Terra Santa  2.594304e-07   
6                    Casa Julio                  Hotel Mamá  4.230585e-07   
7                   Serendipity                   Ca'n Cera  4.670673e-07   
8      Restaurant Santa Eulàlia                  Hotel Mamá  5.172641e-07   
13                   Quina Creu          Posada Terra Santa  4.477991e-07   
14                         Tast                  Hotel Born  9.247864e-07   
16                   Casa Julio                  Hotel Mamá  4.230585e-07   
17                    Tast Club                  Hotel Born  2.236545e-07   
18               La Tortillería          Posada Terra Santa  2.594304e-07   
19                Plaer Natural          Posada Terra Santa  2.440541e-07   
21                  Molta Barra          Posada Terra Santa  1.639656e-07   
22                         Fera                  Hotel Born  6.970462e-07   
27                      Aromata                  Hotel Born  7.089936e-07   
29                    Marc Fosh  Hotel Convent de la Missió  3.770812e-08   
30                     Bruselas           Puro Oasis Urbano  8.078872e-07   
31                      5 Jotas                  Hotel Born  3.392704e-07   
37                         Fera                  Hotel Born  6.970462e-07   
38                 El Aquanauta           Hotel Hostal Cuba  8.490304e-07   
39                      Aromata                  Hotel Born  7.089936e-07   
46                       Horapa           Hotel Hostal Cuba  7.994855e-08   
48                    Tast Club                  Hotel Born  2.236545e-07   
53                          Koh           Hotel Hostal Cuba  7.515671e-07   
58                      Bar Dia           Puro Oasis Urbano  7.175678e-08   
59                 Peix Vermell           Puro Oasis Urbano  6.428009e-07   
60                         Cuba           Hotel Hostal Cuba  2.657486e-08   
61                         Tast                  Hotel Born  9.247864e-07   
64                      Ribello           Puro Oasis Urbano  1.961770e-07   
65                     Bruselas           Puro Oasis Urbano  8.078872e-07   
71                    La Paloma                  Tres Hotel  7.916969e-08   
72                         Nola           Hotel Hostal Cuba  1.130330e-07   
74            Forn de Sant Joan                  Tres Hotel  1.053890e-07   
81                   Quina Creu          Posada Terra Santa  4.477991e-07   
82                         Tast                  Hotel Born  9.247864e-07   
84                   Casa Julio                  Hotel Mamá  4.230585e-07   
85                    Tast Club                  Hotel Born  2.236545e-07   
86               La Tortillería          Posada Terra Santa  2.594304e-07   
87                Plaer Natural          Posada Terra Santa  2.440541e-07   
89                  Molta Barra          Posada Terra Santa  1.639656e-07   
90                         Fera                  Hotel Born  6.970462e-07   
95                      Aromata                  Hotel Born  7.089936e-07   
97                    Marc Fosh  Hotel Convent de la Missió  3.770812e-08   
98                     Bruselas           Puro Oasis Urbano  8.078872e-07   
99                      5 Jotas                  Hotel Born  3.392704e-07   
103                   Marc Fosh  Hotel Convent de la Missió  3.770812e-08   
106                   Tast Club                  Hotel Born  2.236545e-07   
108                  Quina Creu          Posada Terra Santa  4.477991e-07   
111                        Fera                  Hotel Born  6.970462e-07   
112                        Tast                  Hotel Born  9.247864e-07   
113                     Aromata                  Hotel Born  7.089936e-07   
114              La To

In [49]:
map_palma = folium.Map(location=[39.5695818, 2.6500745], zoom_start=15)

# add markers to map
 
for lat, lng, label in zip(fin2['Latitude'], fin2['Longitude'], fin2['Venue']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_palma) 
map_palma